In [10]:
import warnings

warnings.filterwarnings("ignore")

<IPython.core.display.Javascript object>

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import itertools
from sklearn.ensemble import RandomForestRegressor
import datetime
from boruta import BorutaPy
from sklearn.metrics import mean_squared_error

In [3]:
%load_ext nb_black
%matplotlib inline

<IPython.core.display.Javascript object>

In [4]:
train = catalog.load("train_contract_value")
cv = catalog.load("cv_contract_value")
# test = catalog.load('test_contract_value')

[08/13/22 18:31:43] INFO     Loading data from 'train_contract_value' (ParquetDataSet)...       ]8;id=41313;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=138910;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/site-packages/kedro/io/data_catalog.py#343\343]8;;\

[08/13/22 18:31:48] INFO     Loading data from 'cv_contract_value' (ParquetDataSet)...          ]8;id=726244;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/site-packages/kedro/io/data_catalog.py\data_catalog.py]8;;\:]8;id=110823;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/site-packages/kedro/io/data_catalog.py#343\343]8;;\

<IPython.core.display.Javascript object>

In [5]:
train_boruta = train.sample(frac=0.05).drop("index", axis=1)

<IPython.core.display.Javascript object>

In [6]:
y_train = train["log_valor_del_contrato"].values
y_cv = cv["log_valor_del_contrato"].values

<IPython.core.display.Javascript object>

In [7]:
train.drop("log_valor_del_contrato", axis=1, inplace=True)
cv.drop("log_valor_del_contrato", axis=1, inplace=True)

<IPython.core.display.Javascript object>

In [8]:
def gen_rf_hyperparameters():
    n_estimators = max(int(10 ** (np.random.random() * 1.5 + 1)), 1)
    max_depth = np.random.choice([1, 2, 5, 10, 20])
    min_samples_leaf = np.random.randint(1, 100)
    max_features = np.random.random()
    return {
        "n_estimators": n_estimators,
        "max_depth": max_depth,
        "min_samples_leaf": min_samples_leaf,
        "max_features": max_features,
    }

<IPython.core.display.Javascript object>

In [9]:
n_cv = 10
score = np.inf
final_params = None
for i in range(n_cv):
    if i % 2 == 0:
        print(
            f"Iteration {i+1} - {n_cv}: CV - {datetime.datetime.today().strftime('%H:%M:%S')}"
        )
    params = gen_rf_hyperparameters()
    model = RandomForestRegressor(**params)
    model.fit(train,y_train)
    pred = model.predict(cv)
    cv_score = mean_squared_error(y_cv,pred)**0.5
    if cv_score < score:
        score = cv_score
        final_params = params
    print(f"Iteration {i+1} - RMSE :{cv_score}")

Iteration 1 - 10: CV - 18:32:08
Iteration 1 - RMSE :1.1329636699317425
Iteration 2 - RMSE :0.9223361324644834
Iteration 3 - 10: CV - 18:52:00
Iteration 3 - RMSE :0.9184816217216467
Iteration 4 - RMSE :0.9184816217216467
Iteration 5 - 10: CV - 19:10:34
Iteration 5 - RMSE :0.9184816217216467
Iteration 6 - RMSE :0.9184816217216467
Iteration 7 - 10: CV - 19:17:48
Iteration 7 - RMSE :0.9184816217216467
Iteration 8 - RMSE :0.8671300491987731
Iteration 9 - 10: CV - 19:30:51
Iteration 9 - RMSE :0.8671300491987731
Iteration 10 - RMSE :0.8671300491987731


<IPython.core.display.Javascript object>

In [6]:
secop_clean["days_ref"] = secop_clean["fecha_de_firma"].apply(
    lambda x: (x - datetime.date(2000, 1, 1)).days
)

<IPython.core.display.Javascript object>

In [7]:
secop_clean = secop_clean[
    [
        "index",
        "full_contract_description",
        "orden",
        "modalidad_de_contratacion",
        "duration_days",
        "Agricultura",
        "Hidrocarburos",
        "Manufactura",
        "ServiciosPublicos",
        "Construccion",
        "Comercio",
        "Comunicaciones",
        "Financiero",
        "Inmobiliaria",
        "Profesionales",
        "AdministracionPublica",
        "Artisticas",
        "ValorAgregado",
        "Impuestos",
        "PIB",
        "Poblacion",
        "log_valor_del_contrato",
        "dias_adicionados",
        "days_ref",
    ]
].copy()

<IPython.core.display.Javascript object>

In [8]:
secop_clean = pd.get_dummies(
    secop_clean, columns=["orden", "modalidad_de_contratacion"], drop_first=True
)

<IPython.core.display.Javascript object>

In [9]:
ind_split = np.random.permutation(secop_clean.index)

<IPython.core.display.Javascript object>

In [10]:
train = secop_clean.loc[ind_split].iloc[: int(len(secop_clean) * 0.7)].copy()
cv = (
    secop_clean.loc[ind_split]
    .iloc[int(len(secop_clean) * 0.7) : int(len(secop_clean) * 0.85)]
    .copy()
)
test = secop_clean.loc[ind_split].iloc[int(len(secop_clean) * 0.85) :].copy()

<IPython.core.display.Javascript object>

In [11]:
del secop_clean

<IPython.core.display.Javascript object>

In [12]:
features_text = 400

<IPython.core.display.Javascript object>

In [13]:
vectorizer = TfidfVectorizer(max_features=features_text)

<IPython.core.display.Javascript object>

In [15]:
text_df_train = pd.DataFrame(
    columns=[f"feat_text_{i+1}" for i in range(features_text)],
    data=np.array(
        vectorizer.fit_transform(train["full_contract_description"]).todense()
    ),
)

<IPython.core.display.Javascript object>

In [16]:
train = pd.merge(train, text_df_train, how="inner", left_index=True, right_index=True)
del text_df_train

<IPython.core.display.Javascript object>

In [17]:
text_df_cv = pd.DataFrame(
    columns=[f"feat_text_{i+1}" for i in range(features_text)],
    data=np.array(vectorizer.transform(cv["full_contract_description"]).todense()),
)
text_df_test = pd.DataFrame(
    columns=[f"feat_text_{i+1}" for i in range(features_text)],
    data=np.array(vectorizer.transform(test["full_contract_description"]).todense()),
)

<IPython.core.display.Javascript object>

In [18]:
cv = pd.merge(cv, text_df_cv, how="inner", left_index=True, right_index=True)
del text_df_cv
test = pd.merge(test, text_df_test, how="inner", left_index=True, right_index=True)
del text_df_test

<IPython.core.display.Javascript object>

In [19]:
train.drop(["full_contract_description"], axis=1, inplace=True)
cv.drop(["full_contract_description"], axis=1, inplace=True)
test.drop(["full_contract_description"], axis=1, inplace=True)

<IPython.core.display.Javascript object>

In [25]:
y_train = train["log_valor_del_contrato"].values
y_train = train["log_valor_del_contrato"].values
y_train = train["log_valor_del_contrato"].values

<IPython.core.display.Javascript object>

In [31]:
train.drop(["full_contract_description","index"], axis=1, inplace=True)

<IPython.core.display.Javascript object>

In [24]:
train.columns[:25]

Index(['index', 'orden', 'modalidad_de_contratacion', 'duration_days',
       'Agricultura', 'Hidrocarburos', 'Manufactura', 'ServiciosPublicos',
       'Construccion', 'Comercio', 'Comunicaciones', 'Financiero',
       'Inmobiliaria', 'Profesionales', 'AdministracionPublica', 'Artisticas',
       'ValorAgregado', 'Impuestos', 'PIB', 'Poblacion',
       'log_valor_del_contrato', 'dias_adicionados', 'days_ref', 'feat_text_1',
       'feat_text_2'],
      dtype='object')

<IPython.core.display.Javascript object>

In [16]:
train[] = np.array(
    vectorizer.fit_transform(train["full_contract_description"]).todense()
)

[08/13/22 14:34:08] WARNING  /var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_71350/23820 ]8;id=500838;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=850053;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py#109\109]8;;\
                             8139.py:1: PerformanceWarning: DataFrame is highly fragmented.  This                  
                             is usually the result of calling `frame.insert` many times, which has                 
                             poor performance.  Consider joining all columns at once using                         
                             pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe                
                             = frame.copy()`                                                                       
                               train[[f"feat_text_{i+1}" for i in range(features_text)]] =                         
                             np.array(                                                                             
                                                                                                                   

                    WARNING  /var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_71350/23820 ]8;id=685026;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=724074;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py#109\109]8;;\
                             8139.py:1: PerformanceWarning: DataFrame is highly fragmented.  This                  
                             is usually the result of calling `frame.insert` many times, which has                 
                             poor performance.  Consider joining all columns at once using                         
                             pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe                
                             = frame.copy()`                                                                       
                               train[[f"feat_text_{i+1}" for i in range(features_text)]] =                         
                             np.array(                                                                             
                                                                                                                   

                    WARNING  /var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_71350/23820 ]8;id=938961;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=339911;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py#109\109]8;;\
                             8139.py:1: PerformanceWarning: DataFrame is highly fragmented.  This                  
                             is usually the result of calling `frame.insert` many times, which has                 
                             poor performance.  Consider joining all columns at once using                         
                             pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe                
                             = frame.copy()`                                                                       
                               train[[f"feat_text_{i+1}" for i in range(features_text)]] =                         
                             np.array(                                                                             
                                                                                                                   

                    WARNING  /var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_71350/23820 ]8;id=236964;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=714690;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py#109\109]8;;\
                             8139.py:1: PerformanceWarning: DataFrame is highly fragmented.  This                  
                             is usually the result of calling `frame.insert` many times, which has                 
                             poor performance.  Consider joining all columns at once using                         
                             pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe                
                             = frame.copy()`                                                                       
                               train[[f"feat_text_{i+1}" for i in range(features_text)]] =                         
                             np.array(                                                                             
                                                                                                                   

                    WARNING  /var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_71350/23820 ]8;id=295621;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=625746;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py#109\109]8;;\
                             8139.py:1: PerformanceWarning: DataFrame is highly fragmented.  This                  
                             is usually the result of calling `frame.insert` many times, which has                 
                             poor performance.  Consider joining all columns at once using                         
                             pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe                
                             = frame.copy()`                                                                       
                               train[[f"feat_text_{i+1}" for i in range(features_text)]] =                         
                             np.array(                                                                             
                                                                                                                   

...

                    WARNING  /var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_71350/23820 ]8;id=684982;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=947817;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py#109\109]8;;\
                             8139.py:1: PerformanceWarning: DataFrame is highly fragmented.  This                  
                             is usually the result of calling `frame.insert` many times, which has                 
                             poor performance.  Consider joining all columns at once using                         
                             pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe                
                             = frame.copy()`                                                                       
                               train[[f"feat_text_{i+1}" for i in range(features_text)]] =                         
                             np.array(                                                                             
                                                                                                                   

                    WARNING  /var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_71350/23820 ]8;id=420664;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=751074;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py#109\109]8;;\
                             8139.py:1: PerformanceWarning: DataFrame is highly fragmented.  This                  
                             is usually the result of calling `frame.insert` many times, which has                 
                             poor performance.  Consider joining all columns at once using                         
                             pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe                
                             = frame.copy()`                                                                       
                               train[[f"feat_text_{i+1}" for i in range(features_text)]] =                         
                             np.array(                                                                             
                                                                                                                   

                    WARNING  /var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_71350/23820 ]8;id=185144;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=498092;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py#109\109]8;;\
                             8139.py:1: PerformanceWarning: DataFrame is highly fragmented.  This                  
                             is usually the result of calling `frame.insert` many times, which has                 
                             poor performance.  Consider joining all columns at once using                         
                             pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe                
                             = frame.copy()`                                                                       
                               train[[f"feat_text_{i+1}" for i in range(features_text)]] =                         
                             np.array(                                                                             
                                                                                                                   

                    WARNING  /var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_71350/23820 ]8;id=418805;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py\warnings.py]8;;\:]8;id=771801;file:///opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/warnings.py#109\109]8;;\
                             8139.py:1: PerformanceWarning: DataFrame is highly fragmented.  This                  
                             is usually the result of calling `frame.insert` many times, which has                 
                             poor performance.  Consider joining all columns at once using                         
                             pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe                
                             = frame.copy()`                                                                       
                               train[[f"feat_text_{i+1}" for i in range(features_text)]] =                         
                             np.array(                                                                             
                                                                                                                   

<IPython.core.display.Javascript object>

In [ ]:
train

In [17]:
dft = ft.todense()

<IPython.core.display.Javascript object>

In [20]:
np.array(dft)

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

<IPython.core.display.Javascript object>

In [ ]:
asdf = vectorizer.fit_transform(train["full_contract_description"]).todense()

In [ ]:
asdf

In [17]:
np.array(ft.todense())

╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ /var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_70786/4150611251.py:1 in <cell line:  │
│ 1>                                                                                               │
│                                                                                                  │
│ [Errno 2] No such file or directory:                                                             │
│ '/var/folders/89/9jx5xq1j4b979h8c76h2dzjr0000gn/T/ipykernel_70786/4150611251.py'                 │
│                                                                                                  │
│ /opt/homebrew/Caskroom/miniforge/base/envs/dm_project/lib/python3.10/site-packages/scipy/sparse/ │
│ _base.py:764 in __getattr__                                                                      │
│                                                                                                  │
│    761 │   │   elif attr == 'size':                                                              │
│    762 │   │   │   return self.getnnz()                                                          │
│    763 │   │   else:                                                                             │
│ ❱  764 │   │   │   raise AttributeError(attr + " not found")                                     │
│    765 │                                                                                         │
│    766 │   def transpose(self, axes=None, copy=False):                                           │
│    767 │   │   """                                                                               │
│                                                                                                  │
│ ╭──────────────────────────────── locals ────────────────────────────────╮                       │
│ │ attr = 'to_dense'                                                      │                       │
│ │ self = <1158002x176925 sparse matrix of type '<class 'numpy.float64'>' │                       │
│ │        │   │   with 23008513 stored elements in Compressed Sparse Row  │                       │
│ │        format>                                                         │                       │
│ ╰────────────────────────────────────────────────────────────────────────╯                       │
╰──────────────────────────────────────────────────────────────────────────────────────────────────╯
AttributeError: to_dense not found

<IPython.core.display.Javascript object>

In [ ]:
train